In [2]:
# The ultimate target feature: time from one stop to another

# Imports
import pandas as pd
import numpy as np
from datetime import date, datetime
from patsy import dmatrices
import seaborn as sns
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
%matplotlib inline
from sklearn.linear_model import LogisticRegression
from sklearn import metrics
from sklearn.tree import export_graphviz, DecisionTreeRegressor, DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn import preprocessing
from sklearn.pipeline import make_pipeline
from sklearn.model_selection import GridSearchCV, train_test_split, cross_val_score
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.externals import joblib 
from statsmodels.formula.api import ols

# Read csv file into a dataframe.
df = pd.read_csv('csv_data/route4.csv')

/home/ubuntu/anaconda3/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2717: DtypeWarning: Columns (14) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


# 1.0 Data Cleaning 

## 1.1 Rename column names

In [3]:
df = df.rename(columns={'Timeframe': 'Start_date'})

## 1.2 Dropping duplicates

In [4]:
df=df.drop_duplicates(keep='first')

## 1.3 Dropping constant columns or columns with missing data

In [5]:
df = df.drop('Direction', axis=1)
df = df.drop('Unnamed: 0', axis=1)
df = df.drop('Congestion', axis=1)
df[df.Journey_Pattern_ID == 'null']
df = df[df['Journey_Pattern_ID'] != '00040002']
df = df[df['Journey_Pattern_ID'] != '00041002']

## 1.4 Remove rows where bus is not at stop

In [6]:
df = df.loc[(df != 0).all(axis=1), :]

## 1.5 Group to normalise time & remove rows where bus idle at stop

In [7]:
# Create empty column which will hold normalised time
df['normal_time'] = 0

In [8]:
grouped_df = df.groupby(['Vehicle_Journey_ID', 'Start_date'])

In [9]:
def normalize_time(df):
    """Normalise the time for each journey"""
    for i in range(df['Timestamp'].size):
        df['normal_time'].values[i] = (df['Timestamp'].values[i] - df['Timestamp'].values[0]) / 1000000
        
    return df

In [10]:
norm_gb = grouped_df.apply(normalize_time)

In [11]:
grouped_df = norm_gb.groupby(['Vehicle_Journey_ID', 'Start_date'])

In [12]:
def remove_idle_at_stop(df):
    df = df.drop_duplicates(subset='Stop_ID', keep='first')
    
    return df

In [13]:
norm_gb = grouped_df.apply(remove_idle_at_stop)

In [14]:
group_df = norm_gb.groupby(['Vehicle_Journey_ID', 'Start_date'])

/home/ubuntu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: 'Vehicle_Journey_ID' is both a column name and an index level.
Defaulting to column but this will raise an ambiguity error in a future version
  """Entry point for launching an IPython kernel.
/home/ubuntu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning: 'Start_date' is both a column name and an index level.
Defaulting to column but this will raise an ambiguity error in a future version
  """Entry point for launching an IPython kernel.


## 1.6 Add new features

In [15]:
df["Time"] = pd.to_datetime(df['Timestamp']*1000, unit="ns")

In [16]:
df['IsWeekend'] = np.where((df['Time'].dt.dayofweek > 5), 1, 0)

In [17]:
df['HourOfDay'] = df['Time'].dt.hour

In [18]:
df['IsEveningTime'] = np.where((df['Time'].dt.hour > 17), 1, 0)

In [19]:
df['IsPeakTime'] = np.where(((df['HourOfDay'] >= 7) & (df['HourOfDay'] <= 10)) | ((df['HourOfDay'] >= 16) & (df['HourOfDay'] <= 19)), 1, 0)

In [20]:
df['SchoolHoliday'] = np.where((df['Time'].dt.date == datetime(2012, 11, 1).date()) | (

df['Time'].dt.date == datetime(2012, 11, 2).date()) | (

                                       df['Time'].dt.date == datetime(2013, 1, 1).date()) | (

                                       df['Time'].dt.date == datetime(2013, 1, 2).date()) | (

                                       df['Time'].dt.date == datetime(2013, 1, 3).date()) | (

                                       df['Time'].dt.date == datetime(2013, 1, 4).date()), 1, 0)

# 2.0 Merge Datasets

## 2.1 Merge bus stop info

In [21]:
df=df.drop_duplicates(subset='Time', keep='first')

In [22]:
df_bus_stop = pd.read_csv('csv_data/busstopinfo.csv', encoding='latin-1')

In [23]:
df_bus_stop_route4 = df_bus_stop.loc[(df_bus_stop.route1 == '4')]
df_bus_stop_route4.shape

(49, 43)

In [24]:
df_bus_stop_route4 = df_bus_stop_route4.rename(columns={'stopid': 'Stop_ID'})

In [25]:
df_southbound = df.loc[(df.Vehicle_ID == 43048) & (df.Vehicle_Journey_ID == 4909)]

In [26]:
# df[(df.Vehicle_ID == 43048)]["Vehicle_Journey_ID"].unique()

Get northbound order of stops

In [27]:
df_northbound = df.loc[(df.Vehicle_ID == 43048) & (df.Vehicle_Journey_ID == 4572)]

In [28]:
df_bus_stop_route4 = df_bus_stop_route4[['Stop_ID', 'fullname']]
df_bus_stop_route4.columns

Index(['Stop_ID', 'fullname'], dtype='object')

In [29]:
df_south = df_southbound.drop_duplicates(subset='Stop_ID', keep='first')

In [30]:
df_south['stop_order'] = df_south.groupby(['Vehicle_Journey_ID', 'At_Stop', 'Start_date', 'Vehicle_ID'])['Timestamp','Stop_ID'].cumcount().reindex()

/home/ubuntu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [31]:
df_north = df_northbound.drop_duplicates(subset='Stop_ID', keep='first')

In [32]:
df_north['stop_order'] = df_north.groupby(['Vehicle_Journey_ID', 'At_Stop', 'Start_date', 'Vehicle_ID'])['Timestamp','Stop_ID'].cumcount().reindex()

/home/ubuntu/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [33]:
df_order = df_south[['Stop_ID', 'stop_order']]
df_order = df_order.drop_duplicates(subset='Stop_ID', keep='first')

In [34]:
df_order2 = df_north[['Stop_ID', 'stop_order']]
df_order2=df_order2.drop_duplicates(subset='Stop_ID', keep='first')

In [35]:
frames = [df_order, df_order2]
df_order3 = pd.concat(frames)

In [36]:
df_bus_stop_route4= pd.merge(df_order3, df_bus_stop_route4, on=['Stop_ID'])

In [37]:
df = pd.merge(df, df_bus_stop_route4, on=['Stop_ID'])

In [38]:
df = df.rename(columns={'fullname': 'Stop_name'})

## 2.2 Merge weather data

In [39]:
df_weather = pd.read_csv('csv_data/weather_data.csv', encoding='latin-1')

In [40]:
df_weather = df_weather.rename(columns={'Rainfall (Yes or No)': 'Rain'})
df_weather = df_weather.rename(columns={'Temperature C': 'Temperature'})
df_weather = df_weather.rename(columns={'Relative Humidity (%)': 'Humidity'})
df_weather = df_weather.rename(columns={'Over 1mm Rain?': 'Heavy_rain'})
df_weather = df_weather.rename(columns={'Precipitation (mm)': 'Amount_of_rain'})
df_weather = df_weather.rename(columns={'Date': 'Time'})
df_weather['Time'] = pd.to_datetime(df_weather['Time'])
df_weather.sort_values(['Time'], ascending=[True], inplace=True)
df_weather['HourOfDay'] = df_weather['Time'].dt.hour

In [41]:
df.sort_values(['Time'], ascending=[True], inplace=True)
df_weather.sort_values(['Time'], ascending=[True], inplace=True)
df =  pd.merge_asof(df, df_weather, on='Time')

In [42]:
#code from here: https://stackoverflow.com/questions/27313647/merging-two-pandas-dataframes-results-in-duplicate-columns

def drop_y(df):
    # list comprehension of the cols that end with '_y'
    to_drop = [x for x in df if x.endswith('_y')]
    df.drop(to_drop, axis=1, inplace=True)

drop_y(df)
df.columns

Index(['Timestamp', 'LineID', 'Journey_Pattern_ID', 'Start_date',
       'Vehicle_Journey_ID', 'Operator', 'Lon', 'Lat', 'Delay', 'Block_ID',
       'Vehicle_ID', 'Stop_ID', 'At_Stop', 'normal_time', 'Time', 'IsWeekend',
       'HourOfDay_x', 'IsEveningTime', 'IsPeakTime', 'SchoolHoliday',
       'stop_order', 'Stop_name', 'Amount_of_rain', 'Temperature',
       'Vapour Pressure (hPa)                ', 'Humidity',
       'Mean Sea Level Pressure (hPa)', 'Rain', 'Heavy_rain'],
      dtype='object')

In [43]:
def rename_x(df):
    for col in df:
        if col.endswith('_x'):
            df.rename(columns={col:col.rstrip('_x')}, inplace=True)
rename_x(df)

# 3.0 Categorise to continuous and categorical

In [44]:
df['IsWeekend'] = df['IsWeekend'].astype('category')
df['HourOfDay'] = df['HourOfDay'].astype('category')
df['IsEveningTime'] = df['IsEveningTime'].astype('category')
df['SchoolHoliday'] = df['SchoolHoliday'].astype('category')
df['IsPeakTime'] = df['IsPeakTime'].astype('category')
df['Operator'] = df['Operator'].astype('category')
df['At_Stop'] = df['At_Stop'].astype('category')
categorical_columns = df.select_dtypes(['category']).columns

In [45]:
continuous_columns = df.select_dtypes(['int64', 'float64']).columns

# Drop columns no longer needed

In [46]:
df = df.drop('Lat', axis=1)
df = df.drop('Lon', axis=1)
df = df.drop('Block_ID', axis=1)
df = df.drop('Operator', axis=1)

# Create time to destination feature

In [47]:
df['end_time'] =df.groupby(['stop_order','Journey_Pattern_ID', 'Start_date', 'HourOfDay'])['Timestamp'].transform(max)

In [48]:
df['time_diff_to_destination'] = df['end_time'] - df['Timestamp']

In [49]:
df['distance_to_end'] = df.stop_order.max() - df.stop_order

In [50]:
df_train = df[:130000]

In [51]:
df_test = df[130000:]

In [52]:
df_group = df.groupby(['Vehicle_Journey_ID', 'Start_date'])

In [ ]:
for k, g in df_group:
    model = ols('time_diff_to_destination ~ distance_to_end + Rain + Temperature +Humidity + IsWeekend +HourOfDay + SchoolHoliday', g)
    results = model.fit()
    print(results.summary())

/home/ubuntu/anaconda3/lib/python3.6/site-packages/scipy/stats/stats.py:1334: UserWarning: kurtosistest only valid for n>=20 ... continuing anyway, n=13
  "anyway, n=%i" % int(n))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/regression/linear_model.py:1471: RuntimeWarning: divide by zero encountered in double_scalars
  return np.sqrt(eigvals[0]/eigvals[-1])
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/base/model.py:1036: RuntimeWarning: divide by zero encountered in true_divide
  return self.params / self.bse
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/base/model.py:1036: RuntimeWarning: invalid value encountered in true_divide
  return self.params / self.bse
/home/ubuntu/anaconda3/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:879: RuntimeWarning: invalid value encountered in greater
  return (self.a < x) & (x < self.b)
/home/ubuntu/anaconda3/lib/python3.6/site-packages/scipy/stats/_distn_infrastructure.py:879: R

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.983
Model:                                  OLS   Adj. R-squared:                  0.981
Method:                       Least Squares   F-statistic:                     629.9
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):           4.62e-11
Time:                              13:27:55   Log-Likelihood:                -249.21
No. Observations:                        13   AIC:                             502.4
Df Residuals:                            11   BIC:                             503.6
Df Model:                                 1                                         
Covariance Type:                  nonrobust                                         
                          coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------

/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/stats/stattools.py:72: ValueWarning: omni_normtest is not valid with less than 8 observations; 5 samples were given.
  "samples were given." % int(n), ValueWarning)
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/regression/linear_model.py:1396: RuntimeWarning: invalid value encountered in double_scalars
  return self.ess/self.df_model
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/stats/stattools.py:72: ValueWarning: omni_normtest is not valid with less than 8 observations; 3 samples were given.
  "samples were given." % int(n), ValueWarning)
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/stats/stattools.py:72: ValueWarning: omni_normtest is not valid with less than 8 observations; 2 samples were given.
  "samples were given." % int(n), ValueWarning)
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/regression/linear_model.py:1392: RuntimeWarning: divide by zero e

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.571
Model:                                  OLS   Adj. R-squared:                  0.428
Method:                       Least Squares   F-statistic:                     3.992
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):              0.140
Time:                              13:27:55   Log-Likelihood:                -109.31
No. Observations:                         5   AIC:                             222.6
Df Residuals:                             3   BIC:                             221.8
Df Model:                                 1                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

/home/ubuntu/anaconda3/lib/python3.6/site-packages/scipy/stats/stats.py:1334: UserWarning: kurtosistest only valid for n>=20 ... continuing anyway, n=18
  "anyway, n=%i" % int(n))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/scipy/stats/stats.py:1334: UserWarning: kurtosistest only valid for n>=20 ... continuing anyway, n=14
  "anyway, n=%i" % int(n))
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/stats/stattools.py:72: ValueWarning: omni_normtest is not valid with less than 8 observations; 7 samples were given.
  "samples were given." % int(n), ValueWarning)
/home/ubuntu/anaconda3/lib/python3.6/site-packages/statsmodels/stats/stattools.py:72: ValueWarning: omni_normtest is not valid with less than 8 observations; 4 samples were given.
  "samples were given." % int(n), ValueWarning)


...

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.187
Model:                                  OLS   Adj. R-squared:                  0.025
Method:                       Least Squares   F-statistic:                     1.152
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):              0.332
Time:                              13:28:28   Log-Likelihood:                -150.66
No. Observations:                         7   AIC:                             305.3
Df Residuals:                             5   BIC:                             305.2
Df Model:                                 1                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.659
Model:                                  OLS   Adj. R-squared:                  0.583
Method:                       Least Squares   F-statistic:                     8.692
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):            0.00791
Time:                              13:28:28   Log-Likelihood:                -259.37
No. Observations:                        12   AIC:                             524.7
Df Residuals:                             9   BIC:                             526.2
Df Model:                                 2                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.557
Model:                                  OLS   Adj. R-squared:                  0.539
Method:                       Least Squares   F-statistic:                     30.22
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):           3.20e-09
Time:                              13:28:28   Log-Likelihood:                -1059.6
No. Observations:                        51   AIC:                             2125.
Df Residuals:                            48   BIC:                             2131.
Df Model:                                 2                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.084
Model:                                  OLS   Adj. R-squared:                  0.052
Method:                       Least Squares   F-statistic:                     2.653
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):              0.114
Time:                              13:28:28   Log-Likelihood:                -623.24
No. Observations:                        31   AIC:                             1250.
Df Residuals:                            29   BIC:                             1253.
Df Model:                                 1                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

                               OLS Regression Results                               
Dep. Variable:     time_diff_to_destination   R-squared:                       0.997
Model:                                  OLS   Adj. R-squared:                  0.996
Method:                       Least Squares   F-statistic:                     2301.
Date:                      Sat, 24 Jun 2017   Prob (F-statistic):           2.07e-20
Time:                              13:28:28   Log-Likelihood:                -367.87
No. Observations:                        19   AIC:                             741.7
Df Residuals:                            16   BIC:                             744.6
Df Model:                                 2                                         
Covariance Type:                  nonrobust                                         
                         coef    std err          t      P>|t|      [0.025      0.975]
---------------------------------------------------------------

## 8.3 Random Forest Regression - Predicts the delay

In [107]:
y, X = dmatrices('time_diff_to_destination ~ distance_to_end + Temperature + Humidity + HourOfDay +IsWeekend + SchoolHoliday + Vehicle_Journey_ID + Start_date', df, return_type="dataframe") 
y = np.ravel(y)
X.head(5)

Intercept  HourOfDay[T.6]  HourOfDay[T.7]  HourOfDay[T.8]  HourOfDay[T.9]  \
0        1.0             0.0             0.0             1.0             0.0   
1        1.0             0.0             0.0             0.0             1.0   
2        1.0             0.0             0.0             0.0             1.0   
3        1.0             0.0             0.0             0.0             1.0   
4        1.0             0.0             0.0             0.0             1.0   

   HourOfDay[T.10]  HourOfDay[T.11]  HourOfDay[T.12]  HourOfDay[T.13]  \
0              0.0              0.0              0.0              0.0   
1              0.0              0.0              0.0              0.0   
2              0.0              0.0              0.0              0.0   
3              0.0              0.0              0.0              0.0   
4              0.0              0.0              0.0              0.0   

   HourOfDay[T.14]         ...          Start_date[T.2013-01-26]  \
0              0.0         ...                               0.0   
1              0.0         ...                               0.0   
2              0.0         ...                               0.0   
3              0.0         ...                               0.0   
4              0.0         ...                               0.0   

   Start_date[T.2013-01-27]  Start_date[T.2013-01-28]  \
0                       0.0                       0.0   
1                       0.0                       0.0   
2                       0.0                       0.0   
3                       0.0                       0.0   
4                       0.0                       0.0   

   Start_date[T.2013-01-29]  Start_date[T.2013-01-30]  \
0                       0.0                       0.0   
1                       0.0                       0.0   
2                       0.0                       0.0   
3                       0.0                       0.0   
4                       0.0                       0.0   

   Start_date[T.2013-01-31]  distance_to_end  Temperature  Humidity  \
0                       0.0             13.0          2.0      89.0   
1                       0.0              1.0          2.0      89.0   
2                       0.0              0.0          2.0      89.0   
3                       0.0              0.0          2.0      89.0   
4                       0.0              0.0          2.0      89.0   

   Vehicle_Journey_ID  
0             15475.0  
1             15475.0  
2             15475.0  
3             15475.0  
4             15475.0  

[5 rows x 55 columns]

In [108]:
X_train, X_test, y_train, y_test = train_test_split(X, y, 
                                                    test_size=0.2, 
                                                    random_state=123)                                 

In [109]:
scaler = preprocessing.StandardScaler().fit(X_train)

In [110]:
pipeline = make_pipeline(preprocessing.StandardScaler(), 
                         RandomForestRegressor(n_estimators=10))

In [111]:
hyperparameters = { 'randomforestregressor__max_features' : ['auto', 'sqrt', 'log2'],
                  'randomforestregressor__max_depth': [None, 5, 3, 1]}

In [112]:
clf = GridSearchCV(pipeline, hyperparameters, cv=10)

In [113]:
clf.fit(X_train, y_train)

GridSearchCV(cv=10, error_score='raise',
       estimator=Pipeline(steps=[('standardscaler', StandardScaler(copy=True, with_mean=True, with_std=True)), ('randomforestregressor', RandomForestRegressor(bootstrap=True, criterion='mse', max_depth=None,
           max_features='auto', max_leaf_nodes=None,
           min_impurity_split=1e-07, min_samples_leaf=1,
           min_samples_split=2, min_weight_fraction_leaf=0.0,
           n_estimators=10, n_jobs=1, oob_score=False, random_state=None,
           verbose=0, warm_start=False))]),
       fit_params={}, iid=True, n_jobs=1,
       param_grid={'randomforestregressor__max_features': ['auto', 'sqrt', 'log2'], 'randomforestregressor__max_depth': [None, 5, 3, 1]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score=True,
       scoring=None, verbose=0)

In [114]:
pred = clf.predict(X_test)

In [115]:
r2_score(y_test, pred)

0.87947202118321255

Good, closer to 1 the better

In [116]:
mean_squared_error(y_test, pred)

1.2669050800009099e+17

Good, closer to 0 the better

This saves the model for later

In [117]:
joblib.dump(clf, '../flask_app/static/rf_regressor.pkl')

['../flask_app/static/rf_regressor.pkl']

In [118]:
X_test.head()

Intercept  HourOfDay[T.6]  HourOfDay[T.7]  HourOfDay[T.8]  \
4393         1.0             0.0             0.0             1.0   
25426        1.0             0.0             0.0             0.0   
30538        1.0             0.0             0.0             0.0   
7722         1.0             0.0             0.0             0.0   
43135        1.0             0.0             0.0             0.0   

       HourOfDay[T.9]  HourOfDay[T.10]  HourOfDay[T.11]  HourOfDay[T.12]  \
4393              0.0              0.0              0.0              0.0   
25426             0.0              0.0              0.0              0.0   
30538             0.0              0.0              0.0              0.0   
7722              0.0              0.0              0.0              0.0   
43135             0.0              0.0              0.0              1.0   

       HourOfDay[T.13]  HourOfDay[T.14]         ...          \
4393               0.0              0.0         ...           
25426              0.0              0.0         ...           
30538              0.0              1.0         ...           
7722               0.0              1.0         ...           
43135              0.0              0.0         ...           

       Start_date[T.2013-01-26]  Start_date[T.2013-01-27]  \
4393                        0.0                       0.0   
25426                       0.0                       0.0   
30538                       0.0                       0.0   
7722                        0.0                       0.0   
43135                       0.0                       0.0   

       Start_date[T.2013-01-28]  Start_date[T.2013-01-29]  \
4393                        0.0                       0.0   
25426                       0.0                       0.0   
30538                       0.0                       0.0   
7722                        0.0                       0.0   
43135                       1.0                       0.0   

       Start_date[T.2013-01-30]  Start_date[T.2013-01-31]  distance_to_end  \
4393                        0.0                       0.0              7.0   
25426                       0.0                       0.0              7.0   
30538                       0.0                       0.0              3.0   
7722                        0.0                       0.0             12.0   
43135                       0.0                       0.0              0.0   

       Temperature  Humidity  Vehicle_Journey_ID  
4393           5.8      82.0              4557.0  
25426          3.1      81.0              4580.0  
30538          2.6      88.0              4562.0  
7722           5.8      82.0              4900.0  
43135          9.1      78.0              4939.0  

[5 rows x 55 columns]

This can then be reloaded to be used in the flask app. As seen below.

In [119]:
clf2 = joblib.load('../flask_app/static/rf_regressor.pkl')

In [120]:
clf2.predict(X_test)

array([  3.36824878e+09,   6.78683333e+08,   5.85500000e+08, ...,
         1.45500000e+08,   2.75255000e+09,   1.77530129e+08])

In [121]:
rfc = RandomForestClassifier(n_estimators=100, max_features='auto', oob_score=True, random_state=1)

In [122]:
df.shape

(47556, 28)

# To Do

Date is in the model as a variable making significant impact as cannot group random forest by dates - to confirm why it makes an impact (improves score about 7% but we should  understand is this equiv to groupby or coincidence or a proxy for events).

Getting a memory error with feature importance so for now using the linear results to guide - issue with rain: clearly important - we know that - and humidity is important, but no rain columns are making any impact. See commented out code below.

In [123]:
#rfc.fit(X_train, y_train)

In [124]:
#pd.DataFrame({'feature': X_train.columns, 'importance':rfc.feature_importances_})